In [1]:
from spacecraft.satellite import SatelliteImplementation
from setup.initial_settings import SimulationSetupReader
from setup.two_line_element import TwoLineElementReader
from visualziations.visualizations import plot_orbit, plot_lla, plot_position, plot_magnetic_field_eci, plot_magnetic_field_sbf, plot_sun_vector_eci, plot_sun_vector_sbf
from visualziations.visualizations import plot_angular_velocity, plot_euler_angles, plot_pointing_error, plot_torque, plot_angular_acceleration
from spacecraft.sensors import MagnetometerImplementation, SunsensorImplementation, SensorFusionImplementation
import core.transformations as tr
import core.utilities as ut
from pathlib import Path

import numpy as np

setup = SimulationSetupReader(Path('setup/initial_settings.json'))
tle = TwoLineElementReader(Path('setup/tle'))
magnetometer = MagnetometerImplementation(noise=True)
sunsensor = SunsensorImplementation(noise=True)
sensor_fusion = SensorFusionImplementation(['triad', 'quest', 'ekf'], tr.euler_xyz_to_quaternion(setup.euler_angles))

satellite = SatelliteImplementation(setup, tle, magnetometer, sunsensor, sensor_fusion)

state_vector = ut.initialize_state_vector(satellite)
n_iter = 15000
for x in range(1, n_iter, 1):
    satellite.update_iteration(x)
    satellite.apply_rotation()  # applying rotation is required for triad and quest

    mag_field_sbf, mag_field_eci = satellite.magnetic_field
    sun_vector_sbf, sun_vector_eci = satellite.sun_vector
    # print(f"Sun vector SBF and ECI {sun_vector_sbf}, {sun_vector_eci}")
    if x % 100 == 0:
        print(f"Iteration {x} of {n_iter}")
        # print(f"Magnetic field (SBF): {mag_field_sbf}")
        # print(f"Magnetic field (ECI): {mag_field_eci}")
    # print(f"Reference quaternion: {q_ref}"

    satellite.apply_triad(
        ut.normalize(mag_field_eci), ut.normalize(sun_vector_eci), 
        ut.normalize(mag_field_sbf), ut.normalize(sun_vector_sbf)
    )
    # q_triad = satellite.quaternion.copy()
    # print(f"Quaternion after TRIAD: {q_triad}")
    # print(f"Rotation {np.arccos(q_triad[3]) * 2 * 180 / np.pi}")

    # satellite.apply_quest(
    #     [ut.normalize(mag_field_sbf), ut.normalize(sun_vector_sbf)],
    #     [ut.normalize(mag_field_eci), ut.normalize(sun_vector_eci)]
    # )
    # # q_quest = satellite.quaternion.copy()
    # print(f"Quaternion after QUEST: {q_quest}")

    # ekf automatically updates the quaternion by the obtained rotation
    # satellite.apply_ekf(
    #     [ut.normalize(mag_field_sbf), ut.normalize(sun_vector_sbf)],
    #     [ut.normalize(mag_field_eci), ut.normalize(sun_vector_eci)]
    # )
    # q_ekf = satellite.quaternion 

    satellite.apply_detumbling(
        method='b_dot', 
        adapt_velocity=False, 
        adapt_magnetic=False, 
        proportional=False, 
        modified=False
    )
    # satellite.apply_pointing('b_cross', 'earth_pointing', align_axis=[0, 0, 1])
    # print(f"Quaternion after EKF: {q_ekf}")
    state_vector = ut.update_state_vector(satellite, state_vector)


print(state_vector) 
plot_orbit(state_vector, setup)
plot_position(state_vector)
plot_lla(state_vector)
plot_magnetic_field_eci(state_vector)
plot_magnetic_field_sbf(state_vector) 
plot_angular_velocity(state_vector)
plot_euler_angles(state_vector)
plot_pointing_error(state_vector)
plot_torque(state_vector)
plot_angular_acceleration(state_vector)
plot_sun_vector_eci(state_vector)
plot_sun_vector_sbf(state_vector)


Gain: -10000
Angular velocity deg/s: [10. 10.  0.]
Magnetic field (T): [ 1.96036723e-05 -4.41620270e-09 -3.00760027e-05]
Filetered derivative [-4.86430119e-06  4.84658280e-06 -4.24353482e-06]
Modified item [-5.24925272e-06  5.24925272e-06 -3.42225704e-06]
Magnetic dipole moment b-dot: [ 0.04864301 -0.04846583  0.04243535]
Magnetic dipole moment b-dot modified: [ 0.05249253 -0.05249253  0.03422257]
Gain: -10000
Angular velocity deg/s: [ 9.99803523e+00  9.99675506e+00 -6.40084153e-04]
Magnetic field (T): [ 1.41346150e-05  5.44088274e-06 -3.25281054e-05]
Filetered derivative [-5.40858165e-06  5.38542733e-06 -2.63124597e-06]
Modified item [-5.67532238e-06  5.67595204e-06 -1.51672859e-06]
Magnetic dipole moment b-dot: [ 0.05408582 -0.05385427  0.02631246]
Magnetic dipole moment b-dot modified: [ 0.05675322 -0.05675952  0.01516729]
Gain: -10000
Angular velocity deg/s: [ 9.99626597e+00  9.99370719e+00 -1.27939239e-03]
Magnetic field (T): [ 8.42416498e-06  1.11254295e-05 -3.30233292e-05]
Filet

In [17]:
import numpy as np
import core.transformations as tr

euler = np.array([0, 0, 180])

quat = tr.euler_xyz_to_quaternion(euler)
print(f"Quaternion: {quat}")
new_euler = tr.quaternion_to_euler_xyz(quat)
print(f"New Euler: {new_euler}")

Quaternion: [0.00000000e+00 0.00000000e+00 1.00000000e+00 6.12303177e-17]
New Euler: [  0.   0. 180.]


In [7]:
import numpy as np
#                      x                 y                   z              x               y
array1 = np.array([-0.0114, -        -0.0114,          0.0114]) #         -0.0114, -        0.0114
array2 = np.array([ 1.92709051e-05, -3.48258106e-05,  1.31687787e-05]) # 1.92709051e-05, -3.48258106e-05

array3 = [
    (array1[1]*array2[2] - array1[2]*array2[1]),
    (array1[2]*array2[0] - array1[0]*array2[2]),
    (array1[0]*array2[1] - array1[1]*array2[0])
]

array3_np = np.cross(array1, array2)    

print(array3)
print(array3_np)


[np.float64(5.4713831802e-07), np.float64(3.6981239532e-07), np.float64(1.7732592269999998e-07)]
[5.47138318e-07 3.69812395e-07 1.77325923e-07]
